In [1]:
import matplotlib
matplotlib.use('Agg')
import matplotlib.pyplot as plt
import trimesh
import argparse
import os
import time
import numpy as np
import torch
import torch.optim as optim
import lib.utils as utils
from lib.utils import standard_normal_logprob
from lib.utils import count_nfe, count_total_time
from lib.utils import build_model_tabular
import pandas as pd
import random
from lib.visualize_flow import visualize_transform
import lib.layers.odefunc as odefunc
from matplotlib import pyplot as plt
%matplotlib inline 
import glob

In [2]:
SOLVERS = ["dopri5"]
parser = argparse.ArgumentParser('SoftFlow')
parser.add_argument(
    '--data', choices=['2spirals_1d','2spirals_2d', 'swissroll_1d','swissroll_2d', 'circles_1d', 'circles_2d', '2sines_1d', 'target_1d'],
    type=str, default='3d_microgel'
)
parser.add_argument("--layer_type", type=str, default="concatsquash", choices=["concatsquash"])
parser.add_argument('--dims', type=str, default='64-64-64')
parser.add_argument("--num_blocks", type=int, default=1, help='Number of stacked CNFs.')
parser.add_argument('--time_length', type=float, default=0.5)
parser.add_argument('--train_T', type=eval, default=True)
parser.add_argument("--divergence_fn", type=str, default="brute_force", choices=["brute_force", "approximate"])
parser.add_argument("--nonlinearity", type=str, default="tanh", choices=odefunc.NONLINEARITIES)

parser.add_argument('--solver', type=str, default='dopri5', choices=SOLVERS)
parser.add_argument('--atol', type=float, default=1e-5)
parser.add_argument('--rtol', type=float, default=1e-5)

parser.add_argument('--residual', type=eval, default=False, choices=[True, False])
parser.add_argument('--rademacher', type=eval, default=False, choices=[True, False])
parser.add_argument('--spectral_norm', type=eval, default=False, choices=[True, False])
parser.add_argument('--niters', type=int, default=100000)
parser.add_argument('--batch_size', type=int, default=100)
parser.add_argument('--test_batch_size', type=int, default=1000)
parser.add_argument('--lr', type=float, default=1e-3)
parser.add_argument('--weight_decay', type=float, default=1e-5)

# for the proposed method
parser.add_argument('--std_min', type=float, default=0.0)
parser.add_argument('--std_max', type=float, default=0.1)
parser.add_argument('--std_weight', type=float, default=2)

parser.add_argument('--viz_freq', type=int, default=100)
parser.add_argument('--val_freq', type=int, default=400)
parser.add_argument('--log_freq', type=int, default=10)
parser.add_argument('--gpu', type=int, default=0)
# args = parser.parse_args()
args, unknown = parser.parse_known_args()


In [3]:
# logger
args.data = "microgel_multiclass"
save_path = './results/' + args.data + '/SoftFlow'
utils.makedirs(save_path)

device = torch.device('cuda:' + str(args.gpu) if torch.cuda.is_available() else 'cpu')

In [4]:
def get_transforms(model):

    def sample_fn(z, logpz=None):
        zeors_std = torch.zeros(z.shape[0], 1).to(z)
        if logpz is not None:
            return model(z, zeors_std, logpz, reverse=True)
        else:
            return model(z, zeors_std, reverse=True)

    def density_fn(x, logpx=None):
        zeors_std = torch.zeros(x.shape[0], 1).to(x)
        if logpx is not None:
            return model(x, zeors_std, logpx, reverse=False)
        else:
            return model(x, zeors_std, reverse=False)

    return sample_fn, density_fn

DATA_add = "/home/staff/azad/deeplearning/pointcloud/PAINT_DiffTemp/Core-shell/"
Type     = ['Microgel_plotter_v1_density', 'Microgel_plotter_v2_solvatochromism']

temperature_list = os.listdir(DATA_add)
temperature_list.sort()
temperature_list.remove('35C')

def get_data():
    idt = random.randint(0,len(temperature_list)-1)
    DATA_list = glob.glob(DATA_add+ temperature_list[idt]+'/'+Type[0]+"/*.3d")
    temperature = int(temperature_list[0][-3:-1])
    indx = random.randint(0,len(DATA_list)-1)
    DATA = pd.read_csv(DATA_list[indx], delimiter = "\t", header=None)
    DATA = DATA.to_numpy()[:,:4]
    DATA -= np.mean(DATA, axis=0) 
    DATA = (DATA-np.min(DATA, axis=0))/(np.max(DATA, axis=0)-np.min(DATA, axis=0)) 
    newrow = [temperature, temperature, temperature, temperature]
    DATA = np.vstack([newrow, DATA])

    return DATA



def compute_loss(args, model, batch_size=None):
    if batch_size is None: batch_size = args.batch_size
    x = get_data()


    x = torch.from_numpy(x).type(torch.float32).to(device)
    zero = torch.zeros(x.shape[0], 1).to(x)

    # transform to z
    std = (args.std_max - args.std_min) * torch.rand_like(x[:,0]).view(-1,1) + args.std_min
    eps = torch.randn_like(x) * std
    std_in = std / args.std_max * args.std_weight
#     print(x.shape, std_in.shape, zero.shape)
    z, delta_logp = model(x+eps, std_in, zero)

    # compute log q(z)
    logpz = standard_normal_logprob(z).sum(1, keepdim=True)

    logpx = logpz - delta_logp
    loss = -torch.mean(logpx)
    return loss

In [5]:
model = build_model_tabular(args, 4).to(device)

optimizer = optim.Adam(model.parameters(), lr=args.lr, weight_decay=args.weight_decay)

time_meter = utils.RunningAverageMeter(0.93)
loss_meter = utils.RunningAverageMeter(0.93)
nfef_meter = utils.RunningAverageMeter(0.93)
nfeb_meter = utils.RunningAverageMeter(0.93)
tt_meter = utils.RunningAverageMeter(0.93)

end = time.time()
best_loss = float('inf')

In [6]:
LOW = -4
HIGH = 4
def visualize3d(samples, prior_sample, prior_logdensity, n_samples, transform, inverse_transform, memory=100, title1="$x ~ p(x)$", title2="$q(x)$", title3="$x ~ q(x)$", device="cpu", npts = 100):
    ## first one
    fig = plt.figure(figsize=(25,5))
    ax1 = fig.add_subplot(1, 3, 1, projection="3d")
    ax1.scatter(samples[:, 0], samples[:, 1], samples[:, 2], s=1, c='b', marker="s", facecolor="red", lw=0, alpha=1)
    ax1.set_xlabel('X')
    ax1.set_ylabel('Y')
    ax1.set_zlabel('Z')
    ax1.set_title(title1)
    
    ## second one
    side = np.linspace(LOW, HIGH, npts)
    xx, yy, zz = np.meshgrid(side, side, side)
    memory=100
    x = np.hstack([xx.reshape(-1, 1), yy.reshape(-1, 1), zz.reshape(-1, 1)])
    x = torch.from_numpy(x).type(torch.float32).to(device)
    zeros = torch.zeros(x.shape[0], 1).to(x)

    z, delta_logp = [], []
    inds = torch.arange(0, x.shape[0]).to(torch.int64)
    for ii in torch.split(inds, int(memory**2)):
        z_, delta_logp_ = inverse_transform(x[ii], zeros[ii])
        z.append(z_)
        delta_logp.append(delta_logp_)
    z = torch.cat(z, 0)
    delta_logp = torch.cat(delta_logp, 0)

    logpz = prior_logdensity(z).view(z.shape[0], -1).sum(1, keepdim=True)  # logp(z)
    logpx = logpz - delta_logp

    px = np.exp(logpx.detach().cpu().numpy()).reshape(npts, npts,npts)
    ax = fig.add_subplot(1, 3, 2)
    ax.imshow(px[:,:,1])
    ax.set_title(title2)
    
    ## Third one
    z = prior_sample(n_samples, 3).type(torch.float32).to(device)
    zk = []
    inds = torch.arange(0, z.shape[0]).to(torch.int64)
    for ii in torch.split(inds, int(memory**2)):
        zk.append(transform(z[ii]))

    zk = torch.cat(zk, 0).detach().cpu().numpy()

    ax1 = fig.add_subplot(1, 3, 3, projection="3d")
    ax1.scatter(zk[:, 0], zk[:, 1], zk[:, 2], s=1, c='r', marker="s", facecolor="red", lw=0, alpha=1)
    ax1.set_xlabel('X')
    ax1.set_ylabel('Y')
    ax1.set_zlabel('Z')
    ax1.set_title(title3)


In [ ]:
model.train()
for itr in range(1, args.niters + 1):
    optimizer.zero_grad()

    loss = compute_loss(args, model)
    

    loss_meter.update(loss.item())

    total_time = count_total_time(model)
    nfe_forward = count_nfe(model)

    loss.backward()
    optimizer.step()

    nfe_total = count_nfe(model)
    nfe_backward = nfe_total - nfe_forward
    nfef_meter.update(nfe_forward)
    nfeb_meter.update(nfe_backward)

    time_meter.update(time.time() - end)
    tt_meter.update(total_time)

    log_message = (
        'Iter {:04d} | Time {:.4f}({:.4f}) | Loss {:.6f}({:.6f}) | NFE Forward {:.0f}({:.1f})'
        ' | NFE Backward {:.0f}({:.1f}) | CNF Time {:.4f}({:.4f})'.format(
            itr, time_meter.val, time_meter.avg, loss_meter.val, loss_meter.avg, nfef_meter.val, nfef_meter.avg,
            nfeb_meter.val, nfeb_meter.avg, tt_meter.val, tt_meter.avg
        )
    )

    print(log_message)
    
    if itr % args.val_freq == 0 or itr == args.niters:
        with torch.no_grad():
            model.eval()
            test_loss = compute_loss(args, model, batch_size=args.test_batch_size)
            test_nfe = count_nfe(model)
            log_message = '[TEST] Iter {:04d} | Test Loss {:.6f} | NFE {:.0f}'.format(itr, test_loss, test_nfe)
            print(log_message)

            if test_loss.item() < best_loss:
                best_loss = test_loss.item()
                utils.makedirs(save_path)
                torch.save({
                    'args': args,
                    'state_dict': model.state_dict(),
                }, os.path.join(save_path, 'checkpt_solv.pth'))
            model.train()

#     if itr % args.viz_freq == 0:
#         with torch.no_grad():
#             model.eval()
# #             p_samples = toy_data.inf_train_gen(args.data, batch_size=2000)
#             p_samples = get_data()

#             sample_fn, density_fn = get_transforms(model)
#             p_samples = p_samples[1:]
#             plt.figure(figsize=(9, 3))
#             visualize3d(p_samples, torch.randn, standard_normal_logprob, p_samples.shape[0], sample_fn,density_fn, device=device)
#             fig_filename = os.path.join(save_path, 'figs', '{:04d}.jpg'.format(itr))
#             utils.makedirs(os.path.dirname(fig_filename))
#             plt.savefig(fig_filename, format='png')#, dpi=1200)
#             plt.close()
#             model.train()

    end = time.time()

print('Training has finished.')

Iter 0001 | Time 0.7945(0.7945) | Loss 4.723206(4.723206) | NFE Forward 20(20.0) | NFE Backward 26(26.0) | CNF Time 0.5000(0.5000)
Iter 0002 | Time 0.2949(0.7595) | Loss 4.456954(4.704568) | NFE Forward 26(20.4) | NFE Backward 26(26.0) | CNF Time 0.5000(0.5000)
Iter 0003 | Time 0.2961(0.7271) | Loss 4.437889(4.685901) | NFE Forward 26(20.8) | NFE Backward 26(26.0) | CNF Time 0.5000(0.5000)
Iter 0004 | Time 0.2959(0.6969) | Loss 4.367997(4.663648) | NFE Forward 26(21.2) | NFE Backward 26(26.0) | CNF Time 0.5000(0.5000)
Iter 0005 | Time 0.2106(0.6629) | Loss 4.672186(4.664245) | NFE Forward 20(21.1) | NFE Backward 20(25.6) | CNF Time 0.5000(0.5000)
Iter 0006 | Time 0.2468(0.6337) | Loss 4.637042(4.662341) | NFE Forward 20(21.0) | NFE Backward 26(25.6) | CNF Time 0.5000(0.5000)
Iter 0007 | Time 0.2105(0.6041) | Loss 4.583954(4.656854) | NFE Forward 20(20.9) | NFE Backward 20(25.2) | CNF Time 0.5000(0.5000)
Iter 0008 | Time 0.2053(0.5762) | Loss 4.940883(4.676736) | NFE Forward 20(20.9) | 

Iter 0064 | Time 0.2949(0.2809) | Loss 3.721447(3.817741) | NFE Forward 32(26.8) | NFE Backward 26(25.8) | CNF Time 0.5000(0.5000)
Iter 0065 | Time 0.2919(0.2817) | Loss 3.625879(3.804311) | NFE Forward 32(27.1) | NFE Backward 26(25.9) | CNF Time 0.5000(0.5000)
Iter 0066 | Time 0.2692(0.2808) | Loss 3.386261(3.775047) | NFE Forward 26(27.0) | NFE Backward 26(25.9) | CNF Time 0.5000(0.5000)
Iter 0067 | Time 0.2922(0.2816) | Loss 3.303068(3.742009) | NFE Forward 26(27.0) | NFE Backward 26(25.9) | CNF Time 0.5000(0.5000)
Iter 0068 | Time 0.3269(0.2848) | Loss 3.524309(3.726770) | NFE Forward 32(27.3) | NFE Backward 32(26.3) | CNF Time 0.5000(0.5000)
Iter 0069 | Time 0.2676(0.2836) | Loss 3.278681(3.695404) | NFE Forward 26(27.2) | NFE Backward 26(26.3) | CNF Time 0.5000(0.5000)
Iter 0070 | Time 0.3290(0.2868) | Loss 3.432873(3.677026) | NFE Forward 32(27.6) | NFE Backward 32(26.7) | CNF Time 0.5000(0.5000)
Iter 0071 | Time 0.3256(0.2895) | Loss 3.245395(3.646812) | NFE Forward 32(27.9) | 

Iter 0127 | Time 0.5614(0.4887) | Loss 1.279705(1.494950) | NFE Forward 50(44.5) | NFE Backward 56(49.2) | CNF Time 0.5000(0.5000)
Iter 0128 | Time 0.5483(0.4929) | Loss 1.084995(1.466253) | NFE Forward 50(44.9) | NFE Backward 56(49.6) | CNF Time 0.5000(0.5000)
Iter 0129 | Time 0.5488(0.4968) | Loss 1.986875(1.502697) | NFE Forward 50(45.3) | NFE Backward 56(50.1) | CNF Time 0.5000(0.5000)
Iter 0130 | Time 0.5780(0.5025) | Loss 1.086920(1.473592) | NFE Forward 50(45.6) | NFE Backward 56(50.5) | CNF Time 0.5000(0.5000)
Iter 0131 | Time 0.5901(0.5086) | Loss 0.572651(1.410527) | NFE Forward 50(45.9) | NFE Backward 56(50.9) | CNF Time 0.5000(0.5000)
Iter 0132 | Time 0.5628(0.5124) | Loss 1.902165(1.444941) | NFE Forward 50(46.2) | NFE Backward 56(51.2) | CNF Time 0.5000(0.5000)
Iter 0133 | Time 0.6180(0.5198) | Loss 0.875969(1.405113) | NFE Forward 50(46.5) | NFE Backward 56(51.6) | CNF Time 0.5000(0.5000)
Iter 0134 | Time 0.5220(0.5199) | Loss 0.595653(1.348451) | NFE Forward 38(45.9) | 

Iter 0190 | Time 0.5780(0.5616) | Loss 0.021169(0.285696) | NFE Forward 50(48.0) | NFE Backward 62(60.3) | CNF Time 0.5000(0.5000)
Iter 0191 | Time 0.5770(0.5627) | Loss 2.282166(0.425449) | NFE Forward 50(48.1) | NFE Backward 62(60.4) | CNF Time 0.5000(0.5000)
Iter 0192 | Time 0.5742(0.5635) | Loss -0.134286(0.386267) | NFE Forward 50(48.2) | NFE Backward 62(60.5) | CNF Time 0.5000(0.5000)
Iter 0193 | Time 0.5428(0.5620) | Loss 0.273337(0.378362) | NFE Forward 44(47.9) | NFE Backward 62(60.6) | CNF Time 0.5000(0.5000)
Iter 0194 | Time 0.5424(0.5606) | Loss 0.271075(0.370852) | NFE Forward 44(47.7) | NFE Backward 62(60.7) | CNF Time 0.5000(0.5000)
Iter 0195 | Time 0.5764(0.5617) | Loss -0.298804(0.323976) | NFE Forward 50(47.8) | NFE Backward 62(60.8) | CNF Time 0.5000(0.5000)
Iter 0196 | Time 0.5297(0.5595) | Loss 0.429083(0.331334) | NFE Forward 50(48.0) | NFE Backward 56(60.5) | CNF Time 0.5000(0.5000)
Iter 0197 | Time 0.5494(0.5588) | Loss -0.050152(0.304630) | NFE Forward 50(48.1)

Iter 0252 | Time 0.5669(0.5614) | Loss -1.554821(-0.631586) | NFE Forward 44(48.4) | NFE Backward 62(59.9) | CNF Time 0.5000(0.5000)
Iter 0253 | Time 0.5808(0.5628) | Loss -1.234847(-0.673814) | NFE Forward 50(48.5) | NFE Backward 62(60.1) | CNF Time 0.5000(0.5000)
Iter 0254 | Time 0.5784(0.5639) | Loss -0.928823(-0.691665) | NFE Forward 50(48.6) | NFE Backward 62(60.2) | CNF Time 0.5000(0.5000)
Iter 0255 | Time 0.5761(0.5647) | Loss -0.984154(-0.712139) | NFE Forward 50(48.7) | NFE Backward 62(60.3) | CNF Time 0.5000(0.5000)
Iter 0256 | Time 0.6174(0.5684) | Loss -0.665691(-0.708888) | NFE Forward 50(48.8) | NFE Backward 68(60.9) | CNF Time 0.5000(0.5000)
Iter 0257 | Time 0.5769(0.5690) | Loss -1.022560(-0.730845) | NFE Forward 50(48.9) | NFE Backward 62(60.9) | CNF Time 0.5000(0.5000)
Iter 0258 | Time 0.5436(0.5672) | Loss -0.648656(-0.725092) | NFE Forward 44(48.5) | NFE Backward 62(61.0) | CNF Time 0.5000(0.5000)
Iter 0259 | Time 0.5752(0.5678) | Loss -1.081736(-0.750057) | NFE For

...

Iter 55601 | Time 1.0433(0.9768) | Loss -2.831111(-2.614166) | NFE Forward 86(86.0) | NFE Backward 98(97.8) | CNF Time 0.5000(0.5000)
Iter 55602 | Time 1.0694(0.9833) | Loss -2.409229(-2.599820) | NFE Forward 98(86.8) | NFE Backward 98(97.8) | CNF Time 0.5000(0.5000)
Iter 55603 | Time 1.0760(0.9898) | Loss -2.174842(-2.570072) | NFE Forward 92(87.2) | NFE Backward 98(97.8) | CNF Time 0.5000(0.5000)
Iter 55604 | Time 0.9755(0.9888) | Loss -2.984364(-2.599072) | NFE Forward 74(86.3) | NFE Backward 98(97.8) | CNF Time 0.5000(0.5000)
Iter 55605 | Time 1.0199(0.9910) | Loss -2.832295(-2.615398) | NFE Forward 98(87.1) | NFE Backward 98(97.8) | CNF Time 0.5000(0.5000)
Iter 55606 | Time 0.9342(0.9870) | Loss -2.527749(-2.609262) | NFE Forward 74(86.2) | NFE Backward 98(97.9) | CNF Time 0.5000(0.5000)
Iter 55607 | Time 0.9765(0.9863) | Loss -2.684201(-2.614508) | NFE Forward 86(86.2) | NFE Backward 98(97.9) | CNF Time 0.5000(0.5000)
Iter 55608 | Time 1.0277(0.9892) | Loss -2.388577(-2.598693) |

Iter 55663 | Time 0.9838(0.9690) | Loss -2.263301(-2.449761) | NFE Forward 86(84.6) | NFE Backward 98(97.7) | CNF Time 0.5000(0.5000)
Iter 55664 | Time 0.9529(0.9679) | Loss -2.648943(-2.463703) | NFE Forward 80(84.3) | NFE Backward 98(97.7) | CNF Time 0.5000(0.5000)
Iter 55665 | Time 1.0452(0.9733) | Loss -2.297922(-2.452099) | NFE Forward 92(84.8) | NFE Backward 98(97.7) | CNF Time 0.5000(0.5000)
Iter 55666 | Time 0.9632(0.9726) | Loss -2.119605(-2.428824) | NFE Forward 80(84.5) | NFE Backward 98(97.8) | CNF Time 0.5000(0.5000)
Iter 55667 | Time 1.0195(0.9759) | Loss -2.815525(-2.455893) | NFE Forward 92(85.0) | NFE Backward 98(97.8) | CNF Time 0.5000(0.5000)
Iter 55668 | Time 1.0027(0.9778) | Loss -2.122090(-2.432527) | NFE Forward 92(85.5) | NFE Backward 98(97.8) | CNF Time 0.5000(0.5000)
Iter 55669 | Time 0.9911(0.9787) | Loss -2.699254(-2.451198) | NFE Forward 92(86.0) | NFE Backward 98(97.8) | CNF Time 0.5000(0.5000)
Iter 55670 | Time 0.9761(0.9785) | Loss -2.410725(-2.448365) |

Iter 55725 | Time 0.9213(0.9591) | Loss -2.149395(-2.650336) | NFE Forward 74(82.7) | NFE Backward 98(98.2) | CNF Time 0.5000(0.5000)
Iter 55726 | Time 1.0216(0.9634) | Loss -2.951342(-2.671407) | NFE Forward 98(83.7) | NFE Backward 98(98.2) | CNF Time 0.5000(0.5000)
Iter 55727 | Time 0.9643(0.9635) | Loss -2.475922(-2.657723) | NFE Forward 74(83.1) | NFE Backward 104(98.6) | CNF Time 0.5000(0.5000)
Iter 55728 | Time 0.9937(0.9656) | Loss -2.954719(-2.678513) | NFE Forward 86(83.3) | NFE Backward 98(98.5) | CNF Time 0.5000(0.5000)
Iter 55729 | Time 0.9606(0.9653) | Loss -2.314973(-2.653065) | NFE Forward 86(83.5) | NFE Backward 98(98.5) | CNF Time 0.5000(0.5000)
Iter 55730 | Time 1.0108(0.9684) | Loss -2.081681(-2.613068) | NFE Forward 98(84.5) | NFE Backward 98(98.5) | CNF Time 0.5000(0.5000)
Iter 55731 | Time 0.9792(0.9692) | Loss -2.279969(-2.589751) | NFE Forward 86(84.6) | NFE Backward 98(98.4) | CNF Time 0.5000(0.5000)
Iter 55732 | Time 1.0056(0.9717) | Loss -1.883918(-2.540343) 

Iter 55787 | Time 0.9830(0.9558) | Loss -2.424855(-2.515139) | NFE Forward 92(83.2) | NFE Backward 98(98.2) | CNF Time 0.5000(0.5000)
Iter 55788 | Time 0.9826(0.9577) | Loss -2.001769(-2.479203) | NFE Forward 86(83.4) | NFE Backward 98(98.2) | CNF Time 0.5000(0.5000)
Iter 55789 | Time 0.9719(0.9587) | Loss -2.812689(-2.502547) | NFE Forward 92(84.0) | NFE Backward 98(98.2) | CNF Time 0.5000(0.5000)
Iter 55790 | Time 0.9899(0.9608) | Loss -2.522089(-2.503915) | NFE Forward 80(83.7) | NFE Backward 98(98.2) | CNF Time 0.5000(0.5000)
Iter 55791 | Time 1.0602(0.9678) | Loss -2.092252(-2.475099) | NFE Forward 92(84.3) | NFE Backward 98(98.2) | CNF Time 0.5000(0.5000)
Iter 55792 | Time 0.9624(0.9674) | Loss -2.711040(-2.491614) | NFE Forward 86(84.4) | NFE Backward 98(98.2) | CNF Time 0.5000(0.5000)
Iter 55793 | Time 0.9229(0.9643) | Loss -2.661632(-2.503516) | NFE Forward 74(83.7) | NFE Backward 98(98.1) | CNF Time 0.5000(0.5000)
Iter 55794 | Time 0.9652(0.9644) | Loss -2.941758(-2.534193) |

Iter 55849 | Time 1.0675(0.9807) | Loss -2.810546(-2.653792) | NFE Forward 110(88.1) | NFE Backward 98(97.6) | CNF Time 0.5000(0.5000)
Iter 55850 | Time 0.9722(0.9801) | Loss -3.134578(-2.687447) | NFE Forward 86(87.9) | NFE Backward 98(97.7) | CNF Time 0.5000(0.5000)
Iter 55851 | Time 1.0527(0.9852) | Loss -2.078863(-2.644846) | NFE Forward 86(87.8) | NFE Backward 98(97.7) | CNF Time 0.5000(0.5000)
Iter 55852 | Time 1.0413(0.9891) | Loss -2.139827(-2.609495) | NFE Forward 86(87.7) | NFE Backward 98(97.7) | CNF Time 0.5000(0.5000)
Iter 55853 | Time 1.0831(0.9957) | Loss -2.540327(-2.604653) | NFE Forward 92(88.0) | NFE Backward 98(97.7) | CNF Time 0.5000(0.5000)
Iter 55854 | Time 1.0145(0.9970) | Loss -2.580656(-2.602973) | NFE Forward 86(87.8) | NFE Backward 98(97.7) | CNF Time 0.5000(0.5000)
Iter 55855 | Time 1.0434(1.0003) | Loss -2.631821(-2.604993) | NFE Forward 98(88.6) | NFE Backward 98(97.8) | CNF Time 0.5000(0.5000)
Iter 55856 | Time 1.0316(1.0025) | Loss -2.893702(-2.625202) 